### Importing Libraries

In [1]:
from pyspark.ml import Pipeline, PipelineModel
from pyspark.sql.functions import *
from pyspark.sql import SparkSession
from pyspark.sql.types import StructType, StructField, IntegerType, StringType
import sparknlp
from sparknlp.pretrained import PretrainedPipeline
from sparknlp.annotator import *
from sparknlp.common import RegexRule
from sparknlp.base import *

# from sparknlp.

VBox()

Starting Spark application


FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

SparkSession available as 'spark'.


FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

### Installing required modules into PySpark session

In [2]:
sc.install_pypi_package("pandas==1.0.3")
sc.install_pypi_package("scipy==1.4.1")
sc.install_pypi_package("matplotlib==3.2.1")
sc.install_pypi_package("seaborn==0.10.1")
sc.install_pypi_package("boto3==1.23.10")
sc.install_pypi_package("tabulate==0.8.9")

VBox()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

  Using cached https://files.pythonhosted.org/packages/4a/6a/94b219b8ea0f2d580169e85ed1edc0163743f55aaeca8a44c2e8fc1e344e/pandas-1.0.3-cp37-cp37m-manylinux1_x86_64.whl

  Using cached https://files.pythonhosted.org/packages/dd/82/c1fe128f3526b128cfd185580ba40d01371c5d299fcf7f77968e22dfcc2e/scipy-1.4.1-cp37-cp37m-manylinux1_x86_64.whl

  Using cached https://files.pythonhosted.org/packages/b2/c2/71fcf957710f3ba1f09088b35776a799ba7dd95f7c2b195ec800933b276b/matplotlib-3.2.1-cp37-cp37m-manylinux1_x86_64.whl
  Using cached https://files.pythonhosted.org/packages/6c/10/a7d0fa5baea8fe7b50f448ab742f26f52b80bfca85ac2be9d35cdd9a3246/pyparsing-3.0.9-py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/5c/f9/695d6bedebd747e5eb0fe8fad57b72fdf25411273a39791cde838d5a8f51/cycler-0.11.0-py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/51/50/9a9a94afa26c50fc5d9127272737806990aa698c7a1c220b8e5075e70304/kiwisolver-1.4.2-cp37-cp37m-manylinux_2_5_x86_64.manylinux1_x

In [3]:
sc.install_pypi_package('smart-open==6.0.0')

VBox()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

  Using cached https://files.pythonhosted.org/packages/09/db/fab79b619923e26cecc5fb460c80f71f99666fe19182d5bb600ec4d6ff10/smart_open-6.0.0-py3-none-any.whl

In [4]:
import boto3
import pyspark.sql.functions as F
import pandas as pd 
from tabulate import tabulate
import re

VBox()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

### Constructing pipeline for the sentiment classification

In [5]:
document = DocumentAssembler()\
    .setInputCol("text")\
    .setOutputCol("document")

embeddings = BertSentenceEmbeddings\
    .pretrained('sent_bert_wiki_books_sst2', 'en') \
    .setInputCols(["document"])\
    .setOutputCol("sentence_embeddings")

sentimentClassifier = ClassifierDLModel.pretrained("classifierdl_bertwiki_finance_sentiment", "en") \
  .setInputCols(["document", "sentence_embeddings"]) \
  .setOutputCol("class")

financial_sentiment_pipeline = Pipeline(stages=[document, embeddings, sentimentClassifier])

light_pipeline = LightPipeline(financial_sentiment_pipeline.fit(spark.createDataFrame([['']]).toDF("text")))

VBox()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

sent_bert_wiki_books_sst2 download started this may take some time.
Approximate size to download 389.7 MB
[OK!]
classifierdl_bertwiki_finance_sentiment download started this may take some time.
Approximate size to download 22.5 MB
[OK!]

### Accessing scraped Reddit data from an s3 bucket and converting to required format

In [52]:
import boto3
import io

s3 = boto3.client('s3')
s3_resource = boto3.resource('s3')
bucket = s3_resource.Bucket('thiyaghessan-wsb')



object_key = 'wsb_batch_2.csv'
bucket_name = 'thiyaghessan-wsb'
csv_obj = s3.get_object(Bucket=bucket_name, Key=object_key)
body = csv_obj['Body']
csv_string = body.read().decode('utf-8')

df = pd.read_csv(io.StringIO(csv_string))
print(df)

text_list = df['text'].to_list()
#text_list

VBox()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

                                                    link  ...        date
0      https://www.reddit.com/r/wallstreetbets/commen...  ...  1621816803
1      https://www.reddit.com/r/wallstreetbets/commen...  ...  1621817468
2      https://www.reddit.com/r/wallstreetbets/commen...  ...  1621821312
3      https://www.reddit.com/r/wallstreetbets/commen...  ...  1621838209
4      https://www.reddit.com/r/wallstreetbets/commen...  ...  1621842146
...                                                  ...  ...         ...
10524  https://www.reddit.com/r/wallstreetbets/commen...  ...  1653778512
10525  https://www.reddit.com/r/wallstreetbets/commen...  ...  1653779062
10526  https://www.reddit.com/r/wallstreetbets/commen...  ...  1653779203
10527  https://www.reddit.com/r/wallstreetbets/commen...  ...  1653780617
10528  https://www.reddit.com/r/wallstreetbets/commen...  ...  1653782054

[10529 rows x 10 columns]

### Defining function to preprocess the scraped posts

In [8]:
def preprocess(text): 
    text.remove('[removed]')
#     text.remove(' removed ') 
    final = [re.sub(r'http\S+', '', t) for t in text]
    final = [re.sub(r"[^a-zA-Z0-9]+", ' ', t) for t in final]
    final = [re.sub("^\d+\s|\s\d+\s|\s\d+$", " ", s) for s in final]
    return final

VBox()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [9]:
test = preprocess(text_list)

VBox()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [9]:
test

VBox()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

['I don t usually share my secret ways of making money but I feel I must This is not a get rich fast scheme but this is better than investing in stocks For some of you cryptocurrencies are stupid but others know what it s all about This is not brand new and will be taking off soon If you need any questions answered about this don t hesitate to ask Do your research on this and you ll see you can get in big before it takes off Link AutoShark to the moon This is not financial advice ', ' Historical Post Earnings Moves MEGA Compilation Week NVDA SNOW CRM COST BBY ZS DKS TD BMO and More amp nbsp What s poppin bull gang Flux here with Week of the Historical Post Earnings Moves MEGA Compilation I hope you all made some good money following the spreadsheet last week cause it s time to do it all again Earnings season is just about over so there is a good chance that this is going to be the final spreadsheet until Q2 rolls around Thank you all for joining me for the ride amp nbsp All that being 

  ### Converting dates of posts from an epoch fprmat to a YYYY-MM-DD format

In [53]:
import time
df['conv_date'] = df['date'].apply(lambda x: time.strftime("%Y-%m-%d ", time.gmtime(x)))

VBox()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

### Transforming the data using the built pipeline

In [54]:
empty_df = spark.createDataFrame([['']]).toDF("text")
df.drop(4489,inplace = True)
pipelineModel = financial_sentiment_pipeline.fit(empty_df)
df_1 = spark.createDataFrame(pd.DataFrame({"text":test, 'date':df['conv_date']}))
result = pipelineModel.transform(df_1)

VBox()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [55]:
result[['class','date']].show()

VBox()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

+--------------------+-----------+
|               class|       date|
+--------------------+-----------+
|[[category, 0, 48...|2021-05-24 |
|[[category, 0, 54...|2021-05-24 |
|[[category, 0, 18...|2021-05-24 |
|[[category, 0, 10...|2021-05-24 |
|[[category, 0, 24...|2021-05-24 |
|[[category, 0, 15...|2021-05-24 |
|[[category, 0, 21...|2021-05-24 |
|[[category, 0, 24...|2021-05-24 |
|[[category, 0, 10...|2021-05-24 |
|[[category, 0, 44...|2021-05-24 |
|[[category, 0, 56...|2021-05-24 |
|[[category, 0, 41...|2021-05-24 |
|[[category, 0, 25...|2021-05-24 |
|[[category, 0, 10...|2021-05-24 |
|[[category, 0, 19...|2021-05-24 |
|[[category, 0, 59...|2021-05-24 |
|[[category, 0, 10...|2021-05-24 |
|[[category, 0, 51...|2021-05-25 |
|[[category, 0, 45...|2021-05-25 |
|[[category, 0, 58...|2021-05-25 |
+--------------------+-----------+
only showing top 20 rows

In [ ]:
result_df = result[['class','date']].toPandas()

VBox()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

KeyboardInterrupt: 

In [58]:
result_df

VBox()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

                                                   class         date
0      [(category, 0, 482, neutral, {'sentence': '0',...  2021-05-24 
1      [(category, 0, 5489, neutral, {'sentence': '0'...  2021-05-24 
2      [(category, 0, 186, positive, {'sentence': '0'...  2021-05-24 
3      [(category, 0, 106, negative, {'sentence': '0'...  2021-05-24 
4      [(category, 0, 240, neutral, {'sentence': '0',...  2021-05-24 
...                                                  ...          ...
10523  [(category, 0, 152, neutral, {'sentence': '0',...  2022-05-28 
10524  [(category, 0, 8, neutral, {'sentence': '0', '...  2022-05-28 
10525  [(category, 0, 1419, neutral, {'sentence': '0'...  2022-05-28 
10526  [(category, 0, 552, neutral, {'sentence': '0',...  2022-05-28 
10527  [(category, 0, 414, neutral, {'sentence': '0',...  2022-05-28 

[10528 rows x 2 columns]

### Collecting necessary data about the sentiment of a post

In [60]:
result_df['class'] = result_df['class'].apply(lambda x: x[0]['result'])

VBox()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

### Final data with the date of a post, and its sentiment

In [61]:
result_df

VBox()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

          class         date
0       neutral  2021-05-24 
1       neutral  2021-05-24 
2      positive  2021-05-24 
3      negative  2021-05-24 
4       neutral  2021-05-24 
...         ...          ...
10523   neutral  2022-05-28 
10524   neutral  2022-05-28 
10525   neutral  2022-05-28 
10526   neutral  2022-05-28 
10527   neutral  2022-05-28 

[10528 rows x 2 columns]

### Storing into an s3 bucket for further analysis

In [65]:
from io import StringIO # python3; python2: BytesIO 
import boto3

bucket = 'pranathi-sentiment' # already created on S3
csv_buffer = StringIO()
result_df.to_csv(csv_buffer,index = False)
s3_resource = boto3.resource('s3')
s3_resource.Object(bucket, 'final_classification.csv').put(Body=csv_buffer.getvalue())

VBox()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

{'ResponseMetadata': {'RequestId': 'GAQ57ZSX2K4R8BE2', 'HostId': 'EmRvb3Achz561iaN6Fr6Ucjq5opVic/OsTWpzpT4muCy/zkHXNGTnRhcXWXAl01FjUWFPxE1Cg8=', 'HTTPStatusCode': 200, 'HTTPHeaders': {'x-amz-id-2': 'EmRvb3Achz561iaN6Fr6Ucjq5opVic/OsTWpzpT4muCy/zkHXNGTnRhcXWXAl01FjUWFPxE1Cg8=', 'x-amz-request-id': 'GAQ57ZSX2K4R8BE2', 'date': 'Tue, 31 May 2022 21:07:31 GMT', 'etag': '"35abf6a57cd59eaa374eb4826c8a71b1"', 'server': 'AmazonS3', 'content-length': '0'}, 'RetryAttempts': 0}, 'ETag': '"35abf6a57cd59eaa374eb4826c8a71b1"'}